In [1]:
%%html
<style>.container{width:99%}</style>

In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
import os
import shutil
import re
import json
from pathlib import Path

import requests
import geopandas as gpd
import boto3
import pandas as pd

from serverless import settings
from serverless.pipeline.data import (
    census_businesspatterns, 
    census_population, 
    tiger
)
from serverless.pipeline import Pipeline
from serverless.utils import download_url

In [4]:
%%time

processed_path = Path(settings.data.processed_path)
pipeline = Pipeline(processed_path)

path: str = '.*/.*'

CPU times: user 415 µs, sys: 5 µs, total: 420 µs
Wall time: 425 µs


In [6]:
pipeline.delete_lambda('serverlessprez_lambda')

{'ResponseMetadata': {'RequestId': '7309ea29-feb9-4c8f-80ff-35117620362d',
  'HTTPStatusCode': 204,
  'HTTPHeaders': {'date': 'Tue, 12 Jul 2022 01:14:42 GMT',
   'content-type': 'application/json',
   'connection': 'keep-alive',
   'x-amzn-requestid': '7309ea29-feb9-4c8f-80ff-35117620362d'},
  'RetryAttempts': 0}}

In [7]:
pipeline.create_lambda(
    '../serverless/lambda_app/app/lambda.py', 
    'serverlessprez_lambda',
    image_uri="639381120660.dkr.ecr.us-east-1.amazonaws.com/serverlessprez:0.2.4"
)

{'ResponseMetadata': {'RequestId': '37eeccbe-d52d-4aa8-aec7-f0bc1ec314b2',
  'HTTPStatusCode': 201,
  'HTTPHeaders': {'date': 'Tue, 12 Jul 2022 01:14:59 GMT',
   'content-type': 'application/json',
   'content-length': '991',
   'connection': 'keep-alive',
   'x-amzn-requestid': '37eeccbe-d52d-4aa8-aec7-f0bc1ec314b2'},
  'RetryAttempts': 0},
 'FunctionName': 'serverlessprez_lambda',
 'FunctionArn': 'arn:aws:lambda:us-east-1:639381120660:function:serverlessprez_lambda',
 'Role': 'arn:aws:iam::639381120660:role/serverlessprez',
 'CodeSize': 0,
 'Description': 'serverlessprez',
 'Timeout': 60,
 'MemorySize': 512,
 'LastModified': '2022-07-12T01:14:59.297+0000',
 'CodeSha256': '22aae9cc2b0794591fb0d32351a171bc32548ec7942d910b0b5d8d903bb7ab0e',
 'Version': '7',
 'TracingConfig': {'Mode': 'PassThrough'},
 'RevisionId': 'cf2f8185-fd0a-42a9-98c1-c0319dd5b96f',
 'State': 'Pending',
 'StateReason': 'The function is being created.',
 'StateReasonCode': 'Creating',
 'PackageType': 'Image',
 'Archi

In [8]:
pipeline.create_api(
    name = 'serverlessprez_lambda-1.0'
)

{'ResponseMetadata': {'RequestId': 'ba328bb2-bbea-478e-8599-57ef7692b941', 'HTTPStatusCode': 201, 'HTTPHeaders': {'date': 'Tue, 12 Jul 2022 01:15:14 GMT', 'content-type': 'application/json', 'content-length': '71', 'connection': 'keep-alive', 'x-amzn-requestid': 'ba328bb2-bbea-478e-8599-57ef7692b941', 'x-amz-apigw-id': 'VIStXL8toAMEdVg='}, 'RetryAttempts': 0}, 'httpMethod': 'GET', 'authorizationType': 'NONE', 'apiKeyRequired': False}


{'ResponseMetadata': {'RequestId': '09fac35f-deb6-42a6-bd92-110f691355a3',
  'HTTPStatusCode': 201,
  'HTTPHeaders': {'date': 'Tue, 12 Jul 2022 01:15:14 GMT',
   'content-type': 'application/json',
   'content-length': '41',
   'connection': 'keep-alive',
   'x-amzn-requestid': '09fac35f-deb6-42a6-bd92-110f691355a3',
   'x-amz-apigw-id': 'VIStbLmnIAMEd5w='},
  'RetryAttempts': 0},
 'id': 'w0csfn',
 'createdDate': datetime.datetime(2022, 7, 11, 21, 15, 14, tzinfo=tzlocal())}

---

In [329]:
pipeline.rest_api_id

'fxlh2hqunf'

In [394]:
%%time
import sys
import urllib.parse
import json
import pandas as pd
import geopandas as gpd
import folium
import requests

sql = urllib.parse.quote_plus(
    """SELECT 
        county.statefp,
        county.countyfp,
        pop.population_2020,
        pop.rural_urban_continuum_code_2013,
        pop.ctyname,
        ST_GeomFromLegacyBinary(county.geometry) as geometry
    FROM serverlessprez.census_population pop
    JOIN serverlessprez.tiger_county county 
        ON county.statefp = pop.st
        AND county.countyfp = pop.cty
    WHERE pop.st = '47';"""
)

url = f'https://fxlh2hqunf.execute-api.us-east-1.amazonaws.com/dev/serverlessprez?sql={sql}'

# df = pd.read_json(url)

CPU times: user 54 µs, sys: 1e+03 ns, total: 55 µs
Wall time: 58.2 µs


In [397]:
url = f"https://fudwob63a0.execute-api.us-east-1.amazonaws.com/dev/serverless_test?sql={sql}"
resp = requests.get(url)

df = pd.DataFrame(resp.json())

In [398]:
df

statefp countyfp population_2020 rural_urban_continuum_code_2013  \
0       47      061         13529.0                             8.0   
1       47      063         64499.0                             3.0   
2       47      065        366207.0                             2.0   
3       47      067          6662.0                             8.0   
4       47      071         26831.0                             6.0   
..     ...      ...             ...                             ...   
90      47      171         17928.0                             3.0   
91      47      175          6168.0                             9.0   
92      47      181         16232.0                             8.0   
93      47      183         32902.0                             7.0   
94      47      185         27351.0                             7.0   

                        ctyname  \
0      Grundy County, Tennessee   
1     Hamblen County, Tennessee   
2    Hamilton County, Tennessee   
3     Hancock County, Tennessee   
4      Hardin County, Tennessee   
..                          ...   
90     Unicoi County, Tennessee   
91  Van Buren County, Tennessee   
92      Wayne County, Tennessee   
93    Weakley County, Tennessee   
94      White County, Tennessee   

                                             geometry  
0   POLYGON ((-85.709418 35.289251, -85.708902 35....  
1   POLYGON ((-83.249431 36.287161, -83.249492 36....  
2   POLYGON ((-85.175227 34.985976, -85.175151 34....  
3   POLYGON ((-83.204071 36.442803, -83.204045 36....  
4   POLYGON ((-88.202959 35.008028, -88.202834 35....  
..                                                ...  
90  POLYGON ((-82.32577 36.119005, -82.325696 36.1...  
91  POLYGON ((-85.360032 35.625674, -85.358387 35....  
92  POLYGON ((-87.71342 35.482606, -87.713526 35.4...  
93  POLYGON ((-88.650863 36.117273, -88.647989 36....  
94  POLYGON ((0 -85.506291, -85.506291 36.081827, ...  

[95 rows x 6 columns]

In [333]:
df['geometry'] = gpd.GeoSeries.from_wkt(df['geometry'])

gdf = gpd.GeoDataFrame(df, geometry="geometry").reset_index()

gdf = gdf.set_crs(epsg = 4326)

color_scale = (gdf['population_2020'].quantile([i/10 for i in range(0, 11, 1)])).tolist()

m = folium.Map(location=[35.59, -86.94], zoom_start=7, tiles='CartoDB positron')

choropleth = folium.Choropleth(
    geo_data=gdf.to_json(),
    name='choropleth',
    data=gdf,
    columns=["ctyname", "population_2020"],
    fill_color='Reds',
    fill_opacity=0.75,
    line_opacity=.6,
    key_on="feature.properties.ctyname",
    legend_name='Population 2020',
    highlight=True,
    reset=True
).add_to(m)

choropleth.geojson.add_child(folium.GeoJsonTooltip(['ctyname', 'population_2020'], labels=False))

m

In [324]:
%%time

import concurrent.futures

FIPS_CODES = [str(i).zfill(2) for i in list(range(0, 65))]

global_df = pd.DataFrame()

def concurrent_sql(fips_code):
    global global_df
    sql = """
        SELECT 
            county.statefp,
            county.countyfp,
            pop.population_2020,
            pop.rural_urban_continuum_code_2013,
            pop.ctyname,
            ST_GeomFromLegacyBinary(county.geometry) as geometry
        FROM serverlessprez.census_population pop
        JOIN serverlessprez.tiger_county county 
            ON county.statefp = pop.st
            AND county.countyfp = pop.cty
        WHERE pop.st = '{}';
    """

    url = f'https://{pipeline.rest_api_id}.execute-api.us-east-1.amazonaws.com/dev/serverlessprez?sql={urllib.parse.quote_plus(sql.format(str(fips_code).zfill(2)))}'
    df = pd.read_json(url)
    if not df.empty:
        global_df = pd.concat([global_df, df])
    
    
with concurrent.futures.ThreadPoolExecutor(max_workers=30) as executor:
    executor.map(concurrent_sql, [str(i).zfill(2) for i in list(range(0, 78))])

CPU times: user 1.55 s, sys: 469 ms, total: 2.02 s
Wall time: 23.9 s


In [326]:
sys.getsizeof(global_df)/1000000

130.049816

In [334]:
class QueryAthena:

    def __init__(self, output_loc='s3://serverlessprez/database/queries'):
        self.output_loc = output_loc

    def execute_query(self, sql, **kwargs):

        full_result_set = []

        query = ath.start_query_execution(
            QueryString=sql,
            ResultConfiguration={'OutputLocation': self.output_loc}
        )

        qid = query['QueryExecutionId']

        query_state = ath.get_query_execution(QueryExecutionId=qid)['QueryExecution']['Status']['State']

        while query_state in ['RUNNING', 'QUEUED']:
            query_state = ath.get_query_execution(QueryExecutionId=qid)['QueryExecution']['Status']['State']

        results_df = pd.read_csv(
            f"{self.output_loc}/{qid}.csv",
            dtype={
                'zip': str,
                'county': str,
                'fipstate': str,
                'fipscty': str
            }
        )

        return results_df

In [348]:
ath = boto3.client('athena')

sql = """
    SELECT 
        county.statefp,
        county.countyfp,
        pop.population_2020,
        pop.rural_urban_continuum_code_2013,
        pop.ctyname,
        ST_GeomFromLegacyBinary(county.geometry) as geometry
    FROM serverlessprez.census_population pop
    JOIN serverlessprez.tiger_county county 
        ON county.statefp = pop.st
        AND county.countyfp = pop.cty
    WHERE pop.st = '47'
    --LIMIT 2;
"""
# df = QueryAthena().execute_query(sql)

In [349]:
full_result_set = []
output_loc='s3://serverlessprez/database/queries'


query = ath.start_query_execution(
    QueryString=sql,
    ResultConfiguration={'OutputLocation': output_loc}
)

qid = query['QueryExecutionId']

query_state = ath.get_query_execution(QueryExecutionId=qid)['QueryExecution']['Status']['State']

while query_state in ['RUNNING', 'QUEUED']:
    query_state = ath.get_query_execution(QueryExecutionId=qid)['QueryExecution']['Status']['State']

# results_df = pd.read_csv(
#     f"{self.output_loc}/{qid}.csv",
#     dtype={
#         'zip': str,
#         'county': str,
#         'fipstate': str,
#         'fipscty': str
#     }
# )

In [350]:
results = ath.get_query_results(QueryExecutionId=qid)

In [362]:
def results_to_df_structured_json(results):
 
    columns = [
        col['Label']
        for col in results['ResultSet']['ResultSetMetadata']['ColumnInfo']
    ]
 
    listed_results = []
    for res in results['ResultSet']['Rows'][1:]:
        values = []
        for field in res['Data']:
            try:
                values.append(list(field.values())[0]) 
            except:
                values.append(list(' '))

        listed_results.append(
            dict(zip(columns, values))
        )
 
    return listed_results

In [363]:
results_json_struct = results_to_df_structured_json(results)
pd.DataFrame(t)

statefp countyfp population_2020 rural_urban_continuum_code_2013  \
0       47      039         11435.0                             9.0   
1       47      043         54315.0                             1.0   
2       47      049         18489.0                             9.0   
3       47      057         23527.0                             2.0   
4       47      059         70152.0                             4.0   
..     ...      ...             ...                             ...   
90      47      171         17928.0                             3.0   
91      47      175          6168.0                             9.0   
92      47      181         16232.0                             8.0   
93      47      183         32902.0                             7.0   
94      47      185         27351.0                             7.0   

                        ctyname  \
0     Decatur County, Tennessee   
1     Dickson County, Tennessee   
2    Fentress County, Tennessee   
3    Grainger County, Tennessee   
4      Greene County, Tennessee   
..                          ...   
90     Unicoi County, Tennessee   
91  Van Buren County, Tennessee   
92      Wayne County, Tennessee   
93    Weakley County, Tennessee   
94      White County, Tennessee   

                                             geometry  
0   POLYGON ((-87.976434 35.506732, -87.976406 35....  
1   POLYGON ((0 -87.178306, -87.178306 36.228262, ...  
2   POLYGON ((-84.852506 36.292433, -84.852417 36....  
3   POLYGON ((-83.381502 36.265431, -83.381297 36....  
4   POLYGON ((-82.785041 35.987096, -82.785074 35....  
..                                                ...  
90  POLYGON ((-82.32577 36.119005, -82.325696 36.1...  
91  POLYGON ((-85.360032 35.625674, -85.358387 35....  
92  POLYGON ((-87.71342 35.482606, -87.713526 35.4...  
93  POLYGON ((-88.650863 36.117273, -88.647989 36....  
94  POLYGON ((0 -85.506291, -85.506291 36.081827, ...  

[95 rows x 6 columns]

In [357]:
len(results['ResultSet']['Rows'])

96

In [4]:
def prep_zipcode_to_county_mapping(inpath, outpath, partition):
    df = pd.read_excel(inpath, engine='openpyxl', dtype={'zip': str, 'county': str})
    df['statefp'] = df['county'].apply(lambda x: x[:2])
    df['countyfp'] = df['county'].apply(lambda x: x[2:])
    df['state'] = df['usps_zip_pref_state'].str.lower()
    df['city'] = df['usps_zip_pref_city'].str.lower()
    df.to_parquet(outpath, index=False, partition_cols=partition)

def shp_to_esri_enclosed_json_input(gdf, geom_type='esriGeometryPolygon'):

    shp_format = json.loads(gdf.to_json())
    esri_enclosed_json_inputs = {}
    esri_enclosed_json_inputs['displayFieldName'] = ''
    esri_enclosed_json_inputs['fieldAliases'] = {k:k for (k,v) in shp_format['features'][0]['properties'].items()}
    esri_enclosed_json_inputs['geometryType'] = geom_type
    esri_enclosed_json_inputs['spatialReference'] = {'wkid': 4269}

    if geom_type == 'esriGeometryPolygon':
        geom_key = 'rings'
    elif geom_type == 'esriGeometryPolyline':
        geom_key = 'paths'

    for jsonfeat in shp_format['features']:

        if jsonfeat['geometry']:

            if 'features' not in esri_enclosed_json_inputs:
                esri_enclosed_json_inputs['features'] = []

            jsonfeat['geometry'] = {
                geom_key: jsonfeat['geometry']['coordinates']
            }

            efeat = {
                'attributes': jsonfeat['properties']
            }

            efeat['geometry'] = jsonfeat['geometry']
            esri_enclosed_json_inputs['features'].append(efeat)

    return esri_enclosed_json_inputs

def partition_geo_data(path, partitions, processed_path, input_df=None, geom_type='esriGeometryPolygon'):

    gdf = input_df if input_df is not None else gpd.read_file(path).to_crs(4269).convert_dtypes()
    
    if partitions:

        grouped = gdf.groupby(partitions, as_index=False)

        for name, group in grouped:
            if isinstance(name, str):
                name = [name]
            filters = list(zip(partitions, name))
            fileid = ''.join([i[1] for i in filters])
            loc = '/'.join([f'{f[0]}={f[1]}'.lower() for f in filters])

            esri_format = shp_to_esri_enclosed_json_input(group, geom_type=geom_type)

            to_path = Path(processed_path/loc)
            to_path.mkdir(parents=True, exist_ok=True)

            with open(to_path/f'{fileid}.geojson', 'w') as file:
                json.dump(esri_format, file)

In [11]:
def tiger():
    zip_extension = '.zip'
    shp_extension = '.shp'
    excel_extensions = ['.xls', '.xlsx']

    for folder, subfolder in settings.etl.tiger.items():

        raw_path = settings.root_path/settings.data.raw_path/subfolder.file_path
        interim_path = settings.root_path/settings.data.interim_path/subfolder.file_path
        processed_path = settings.root_path/settings.data.processed_path/subfolder.file_path

        raw_path.mkdir(parents=True, exist_ok=True)
        processed_path.mkdir(parents=True, exist_ok=True)
        interim_path.mkdir(parents=True, exist_ok=True)

        url = subfolder.url

        for file in subfolder.files:
            raw_file_path = raw_path/file
            processed_file_path = processed_path/file
            interim_file_path = interim_path/file
            raw_file_exists = os.path.isfile(raw_file_path)
            existing_interim_files = [re.sub('\..*', '', i.name) for i in interim_path.iterdir()]
            processed_file_exists = os.path.isfile(processed_file_path)

            file_name_wo_zip = file.replace(zip_extension, '')

            if not raw_file_exists:
                print(f'DOWNLOADING: from {url+file} to {raw_file_path}')
                download_url(url+file, raw_file_path)
                if (zip_extension in file) and (file_name_wo_zip not in existing_interim_files):
                    print(f'UNZIPPING: from {raw_file_path} to {interim_file_path.parent}')
                    shutil.unpack_archive(raw_file_path, interim_file_path.parent)

                if raw_file_path.suffix == zip_extension:
                    interim_file = interim_file_path.parent/(raw_file_path.stem+shp_extension)
                    interim_file_exists = os.path.isfile(interim_file)
                    # if not interim_file_exists:
                    print(f'PARTITIONING: from {interim_file} to {processed_path}')
                    partition_geo_data(interim_file, subfolder.partition_by, processed_path)

            elif raw_file_path.suffix in excel_extensions:
                interim_file = interim_file_path.parent/'data.parquet'
                interim_file_exists = os.path.isfile(interim_file)
                if not interim_file_exists:
                    print(F'PREPPING: from {raw_file_path} to {interim_file}')
                    # prep_zipcode_to_county_mapping(raw_file_path, processed_file_path.parent, subfolder.partition_by)
        print('FINISHED POPULATING RAW, INTERIM, AND PROCESSED DIRECTORIES')
        
    return None

def main():
    tiger()